# UXArray with ICON2 data
UXArray provides a built in grid reader for ICON2 data. This notebook explores reading in ICON2 mesh and explores methods and data structures after loading.

Benefits to our project

* Provides native IO for ICON2 data
* Can convert between lat,lon and cartesian coordinates (x,y,z)
* Provides connectity lookup tables
* Provides mesh subsetting
* Provides neighbor search algorithms

In [16]:
import uxarray as ux

print(ux.__version__)
grid_path="./data/Ocean_Channel_18000x6000_80km.nc"

uxds = ux.open_grid(grid_path)
uxds

2024.8.2


<uxarray.Grid>
Original Grid Type: ICON
Grid Dimensions:
  * n_node: 8584
  * n_edge: 25456
  * n_face: 16872
  * n_max_face_nodes: 3
  * n_max_face_edges: 3
  * n_max_face_faces: 3
  * two: 2
  * n_nodes_per_face: (16872,)
Grid Coordinates (Spherical):
  * node_lon: (8584,)
  * node_lat: (8584,)
  * edge_lon: (25456,)
  * edge_lat: (25456,)
  * face_lon: (16872,)
  * face_lat: (16872,)
Grid Coordinates (Cartesian):
Grid Connectivity Variables:
  * face_node_connectivity: (16872, 3)
  * face_edge_connectivity: (16872, 3)
  * face_face_connectivity: (16872, 3)
  * edge_face_connectivity: (25456, 2)
Grid Descriptor Variables:
  * n_nodes_per_face: (16872,)

In [17]:
uxds.validate()

Validating the mesh...
-No duplicate nodes found in the mesh.
-All nodes are referenced by at least one element.
-No face area is close to zero.
Mesh validation successful.


True

In [8]:
( 
    uxds.plot.edges(color="Blue",line_width=2) 
    * uxds.plot.nodes(color="Red",size=7)
).opts( 
        title="ICON2 Mesh",
        xlim = (-10,10),
        ylim = (-10,10)
    )

:Overlay
   .Path.I   :Path   [x,y]
   .Points.I :Points   [x,y]

Some functions that may be useful

* [`uxarray.Grid.chunk`](https://uxarray.readthedocs.io/en/latest/user_api/generated/uxarray.Grid.chunk.html)
* [`uxarray.Grid.isel`](https://uxarray.readthedocs.io/en/latest/user_api/generated/uxarray.Grid.isel.html)
* [`uxarray.Grid.get_ball_tree`](https://uxarray.readthedocs.io/en/latest/user_api/generated/uxarray.Grid.get_ball_tree.html)
* [`uxarray.Grid.get_kd_tree`](https://uxarray.readthedocs.io/en/latest/user_api/generated/uxarray.Grid.get_kd_tree.html)
* [`uxarray.Grid.construct_face_centers`](https://uxarray.readthedocs.io/en/latest/user_api/generated/uxarray.Grid.get_kd_tree.html) - Example below shows this doesn't exist. However, it appears from the output above that `face_lon` and `face_lat` already exist.

Subsetting the unstructured grid could also be quite useful, if particles are contained within a certain region...

* [`uxarray.Grid.subset`](https://uxarray.readthedocs.io/en/latest/user_api/generated/uxarray.Grid.subset.html)

In [14]:
uxds.construct_face_center(method="welzl")
uxds

AttributeError: 'Grid' object has no attribute 'construct_face_center'

In [20]:
# Generate cartesian coordinates from lat and lon

uxds.face_x
uxds.face_y
uxds.face_z
uxds

<uxarray.Grid>
Original Grid Type: ICON
Grid Dimensions:
  * n_node: 8584
  * n_edge: 25456
  * n_face: 16872
  * n_max_face_nodes: 3
  * n_max_face_edges: 3
  * n_max_face_faces: 3
  * two: 2
  * n_nodes_per_face: (16872,)
Grid Coordinates (Spherical):
  * node_lon: (8584,)
  * node_lat: (8584,)
  * edge_lon: (25456,)
  * edge_lat: (25456,)
  * face_lon: (16872,)
  * face_lat: (16872,)
Grid Coordinates (Cartesian):
  * node_x: (8584,)
  * node_y: (8584,)
  * node_z: (8584,)
  * face_x: (16872,)
  * face_y: (16872,)
  * face_z: (16872,)
Grid Connectivity Variables:
  * face_node_connectivity: (16872, 3)
  * face_edge_connectivity: (16872, 3)
  * face_face_connectivity: (16872, 3)
  * edge_face_connectivity: (25456, 2)
Grid Descriptor Variables:
  * face_areas: (16872,)
  * n_nodes_per_face: (16872,)

In [21]:
# Easily get bounds for each face (in degrees)

uxds.bounds

/home/joe/miniconda3/envs/uop_sandbox/lib/python3.12/site-packages/uxarray/grid/grid.py:893: UserWarning: Constructing of `Grid.bounds` has not been optimized, which may lead to a long execution time.
  warn(
/home/joe/miniconda3/envs/uop_sandbox/lib/python3.12/site-packages/uxarray/grid/geometry.py:443: UserWarning: The given face should not contain both pole points.
  warnings.warn(
/home/joe/miniconda3/envs/uop_sandbox/lib/python3.12/site-packages/uxarray/grid/geometry.py:443: UserWarning: The given face should not contain both pole points.
  warnings.warn(
/home/joe/miniconda3/envs/uop_sandbox/lib/python3.12/site-packages/uxarray/grid/arcs.py:307: RuntimeWarning: divide by zero encountered in scalar divide
  d_a_max = (n1[2] * dot_n1_n2 - n2[2]) / denom
/home/joe/miniconda3/envs/uop_sandbox/lib/python3.12/site-packages/uxarray/grid/geometry.py:443: UserWarning: The given face should not contain both pole points.
  warnings.warn(
/home/joe/miniconda3/envs/uop_sandbox/lib/python3.12/

<xarray.DataArray 'bounds' (n_face: 16872, Two: 2)> Size: 540kB
array([[[-1.04729511, -1.01045378],
        [ 3.14159265,  3.18404661]],

       [[-1.04719755, -1.01045378],
        [ 3.16281963,  3.20527359]],

       [[-1.01055521, -0.97371   ],
        [ 3.16281963,  3.20527359]],

       ...,

       [[ 0.97371   ,  1.01055521],
        [ 4.28784943,  4.33030339]],

       [[ 1.01045378,  1.04719755],
        [ 4.28784943,  4.33030339]],

       [[ 1.01045378,  1.04729511],
        [ 4.30907641,  4.35153036]]])
Coordinates:
    clon     (n_face) float64 135kB -3.12 -3.099 -3.099 ... -1.974 -1.974 -1.953
    clat     (n_face) float64 135kB -1.023 -1.023 -0.986 ... 0.9982 1.035 1.035
Dimensions without coordinates: n_face, Two, Two
Attributes:
    cf_role:                      face_latlon_bounds
    _FillValue:                   -9223372036854775808
    long_name:                    Latitude and Longitude bounds for each face...
    start_index:                  0
    latitude_intervalsIndex:      IntervalIndex([[-1.0472951074486052, -1.010...
    latitude_intervals_name_map:                                             ...